In [13]:
import requests
response = requests.get("https://api.tinkoff.ru/trading/stocks/list?sortType=ByName&orderType=Asc&country=All")
data = response.json()
data

{'payload': {'values': [{'symbol': {'ticker': 'FLWS',
     'symbolType': 'Stock',
     'classCode': 'SPBXM',
     'bcsClassCode': 'SPBXM',
     'isin': 'US68243Q1067',
     'currency': 'USD',
     'lotSize': 1,
     'minPriceIncrement': 0.01,
     'exchange': 'SPB',
     'exchangeShowName': 'СПБ Биржа',
     'exchangeLogoUrl': 'https://invest-brands.cdn-tinkoff.ru/exchanges/SPB_Exchange.png',
     'sessionOpen': '2022-02-28T10:00:00+03:00',
     'sessionClose': '2022-03-01T01:45:00+03:00',
     'showName': '1-800-Flowers.com Inc',
     'logoName': 'US68243Q1067.png',
     'color': '#000000',
     'textColor': '#ffffff',
     'sector': 'Consumer',
     'countryOfRiskBriefName': 'Соединенные Штаты',
     'countryOfRiskLogoUrl': 'https://invest-brands.cdn-tinkoff.ru/countries/flags/US.png',
     'brand': '1-800-Flowers.com',
     'blackout': False,
     'noTrade': False,
     'premarketStartTime': '10:00',
     'premarketEndTime': '10:00',
     'marketStartTime': '10:00',
     'marketEndT

In [15]:
stocks = list(filter(lambda value: value['symbol']['symbolType'] == 'Stock' and value['symbol']['currency'] == 'USD' and value['symbol']['shortIsEnabled'] == True, data['payload']['values']))
print(data['payload']['values'][0])
print(len(stocks))

{'symbol': {'ticker': 'FLWS', 'symbolType': 'Stock', 'classCode': 'SPBXM', 'bcsClassCode': 'SPBXM', 'isin': 'US68243Q1067', 'currency': 'USD', 'lotSize': 1, 'minPriceIncrement': 0.01, 'exchange': 'SPB', 'exchangeShowName': 'СПБ Биржа', 'exchangeLogoUrl': 'https://invest-brands.cdn-tinkoff.ru/exchanges/SPB_Exchange.png', 'sessionOpen': '2022-02-28T10:00:00+03:00', 'sessionClose': '2022-03-01T01:45:00+03:00', 'showName': '1-800-Flowers.com Inc', 'logoName': 'US68243Q1067.png', 'color': '#000000', 'textColor': '#ffffff', 'sector': 'Consumer', 'countryOfRiskBriefName': 'Соединенные Штаты', 'countryOfRiskLogoUrl': 'https://invest-brands.cdn-tinkoff.ru/countries/flags/US.png', 'brand': '1-800-Flowers.com', 'blackout': False, 'noTrade': False, 'premarketStartTime': '10:00', 'premarketEndTime': '10:00', 'marketStartTime': '10:00', 'marketEndTime': '01:45', 'brokerAccountTypesList': ['Tinkoff', 'TinkoffIis', 'OtherAssets'], 'timeToOpen': 86502117, 'isOTC': False, 'bbGlobal': 'BBG000BBR9P6', 'sh

In [12]:
from notebooks.get_candles import day_candles
from datetime import datetime
import pytz

tz = pytz.timezone("Europe/Moscow")
now_date = datetime(2022, 2, 24, 0, 0, 0, 0, tz)
result = []
download_period = 2

for stock in stocks:
  candles = day_candles(stock['symbol']['ticker'], now=now_date, days_period=download_period)
  volume = 0
  range = 0

  for candle in candles:
    date = datetime.fromtimestamp(candle['date'])
    day = date.weekday()
    
    if day != 6 and day != 5:
      one_percent = candle['c'] / 100
      range = (candle['h']-candle['l'])/one_percent
      volume += candle['v']

  work_days = len(candles)
  if volume / work_days >= 1000000:
    result.append({
      "ticker": stock['symbol']['ticker'],
      "range": range,
      "bbGlobal": stock['symbol']['bbGlobal'],
      "sector": stock['symbol']['sector'],
      "volume": volume / work_days
    })


KeyboardInterrupt: 

In [ ]:
import pandas as pd

sorted_stocks = sorted(result, key=lambda x: x['volume'], reverse=True)
df = pd.DataFrame(sorted_stocks)